## Loading data

The upcoming section consists of a few preparatory steps such as: (I.) preparing environment and loading packages necessary for the further steps, (II.) loading sequencing data, (III.) removing outlier and random samples to equalize a number of replicates per group and (IV.) normalizing data using a rarefaction.   

In [56]:
import sys
import copy

sys.path.append("/home/adam/miseq/seqDataClass")

import pandas as pd
import numpy as np
import random

#import seqDataClass.seqDataClass as seqDataClass
import seqDataClass as seqDataClass

In [2]:
data = seqDataClass.seqObject(mappingFile="/home/adam/miseq/ReverseTrans/mapping.csv", 
                              taxonomyFile= "/home/adam/miseq/ReverseTrans/taxonomy.csv", 
                              otuFile="/home/adam/miseq/ReverseTrans/otutab.txt", 
                              taxonomySep=',',
                              sampleNamesColumn="Name")

#print(data.data.sum(axis=0))

# Removing outlier samples
bad_samples = ["Osnat056", "Osnat045", "Osnat055"]

for sample in bad_samples:
    print("Removing bad sample : {}".format(sample))
    data.remove_sample(category="Name", sample=sample)
    
# Randomply removing samples from the data set
TGIRT = ["Osnat037", "Osnat038", "Osnat039", "Osnat040", "Osnat041", "Osnat042", "Osnat043"]

tgirtChoice = random.sample(TGIRT, 1)

for sample in tgirtChoice:
    print("Removing randomly: {} from TGIRT".format(sample))
    data.remove_sample(category="Name", sample=sample)

promega55 = ["Osnat059", "Osnat060", "Osnat061", "Osnat062"]
promega55Choice = random.sample(promega55, 2)   # Randomly select an element from a list

for sample in promega55Choice:
    print("Removing randomly: {} from ImPromII 55°C".format(sample))
    data.remove_sample(category="Name", sample=sample)

data.rarefy_to_even_depth(seqDepth=10000,seed=124)

#print(data.data.sum(axis=0))

data.add_otu_parameter(yamlParamDictFile="/home/adam/miseq/ReverseTrans/GC_content_plot/otus_GC.yaml", paramName="GC_content")

Removing bad sample : Osnat056
Removing bad sample : Osnat045
Removing bad sample : Osnat055
Removing randomly: Osnat039 from TGIRT
Removing randomly: Osnat060 from ImPromII 55°C
Removing randomly: Osnat061 from ImPromII 55°C
Sample Osnat038 was removed from the dataset because it contains insufficient amount of sequences (34).
Sample Osnat048 was removed from the dataset because it contains insufficient amount of sequences (121).


In [57]:
data.save_otu_csv(fileName="/home/adam/miseq/ReverseTrans/normalized_tab.csv")

## Saving data for downstream analysis

Data is normalized by column the results are presented in a table. Following that, only an upper quartile of the classes is further normalized by row (class) and the result is used for the GC relative enrichment plot. 

In [3]:
data.data

Enzyme                                                                                                                                 TGIRT  \
Replicate                                                                                                                                  1   
Name                                                                                                                                Osnat037   
Domain       Phylum            Class               Order                 Family                Genus             OTU     GC_content            
Bacteria     Cyanobacteria     Oxyphotobacteria    Nostocales            Phormidiaceae         Tychonema         Otu0001 0.547847         30   
             Actinobacteria    Actinobacteria      Micrococcales         Micrococcaceae        Unclassified      Otu0002 0.572127        463   
             Proteobacteria    Alphaproteobacteria Azospirillales        Azospirillaceae       Skermanella       Otu0003 0.579208        162   
                               Gammaproteobacteria Betaproteobacteriales Burkholderiaceae      Pelomonas         Otu0004 0.550117         54   
                               Alphaproteobacteria Rhizobiales           uncultured            Unclassified      Otu0005 0.559406        189   
                                                   Sphingomonadales      Sphingomonadaceae     Sphingomonas      Otu0006 0.522277        251   
                                                   Rhizobiales           Beijerinckiaceae      Unclassified      Otu0007 0.564356         47   
                                                                                               Microvirga        Otu0008 0.559406        104   
                                                   Elsterales            uncultured            Unclassified      Otu0009 0.574257         23   
                               Deltaproteobacteria Myxococcales          Unclassified          Unclassified      Otu0010 0.567757        112   
             Actinobacteria    Rubrobacteria       Rubrobacterales       Rubrobacteriaceae     Rubrobacter       Otu0011 0.602804         49   
                               Actinobacteria      Frankiales            Geodermatophilaceae   Blastococcus      Otu0012 0.586797        248   
                                                   Streptomycetales      Streptomycetaceae     Streptomyces      Otu0013 0.581907        130   
                               Rubrobacteria       Rubrobacterales       Rubrobacteriaceae     Rubrobacter       Otu0014 0.593458         24   
                               Actinobacteria      Micromonosporales     Micromonosporaceae    Actinoplanes      Otu0015 0.610294         94   
                                                   Micrococcales         Promicromonosporaceae Promicromonospora Otu0016 0.572127         36   
             Proteobacteria    Alphaproteobacteria Rhizobiales           Xanthobacteraceae     Bradyrhizobium    Otu0017 0.547030        100   
                               Gammaproteobacteria Betaproteobacteriales Burkholderiaceae      Ralstonia         Otu0018 0.533800          0   
                               Deltaproteobacteria Myxococcales          BIrii41               Unclassified      Otu0019 0.565421         14   
                               Gammaproteobacteria Betaproteobacteriales Burkholderiaceae      Aquabacterium     Otu0020 0.545455          0   
                               Alphaproteobacteria Rhodobacterales       Rhodobacteraceae      Rubellimicrobium  Otu0021 0.576733         35   
                                                   Rhizobiales           Beijerinckiaceae      Unclassified      Otu0022 0.576733         38   
                                                   Sphingomonadales      Sphingomonadaceae     Novosphingobium   Otu0023 0.529703          0   
                                                   Acetobacterales       Acetobacteraceae      uncultured       

In [4]:
# A copy of the original data frame
df1 = data.data.copy()

In [5]:
# Calculating a sum per enzyme category to normalize 
df2 = df1.groupby("Class").sum()

# Standard deviation per enzyme group
df2_std = df2.std(level="Enzyme", axis=1)

# Making a sum on the class and enzyme level
#df2 = df1.sum(level="Class", axis=0)
df2_ave = df2.sum(level="Enzyme", axis=1)

In [6]:
df2_ave

Enzyme                  TGIRT  SuperScriptIV  Promega42  Promega55
Class                                                             
0319-7L14                 392            332        527        442
ABY1                        0              0          0          0
AKAU4049                    4              3          0          1
Acidimicrobiia           1858           1518       1203       1617
Acidobacteriia            359            444        257        259
Actinobacteria          11353          10105       5864      11263
Alphaproteobacteria     12385          12148      12943       9302
Anaerolineae               89            113        191        175
Armatimonadia               2              1          6         19
BD2-11                     42             48         26         33
BD7-11                      0              4          7          4
Babeliae                    9             18         11         10
Bacilli                   520            663       1356        656
Bacteroidia              3005           2307       2825       1817
Berkelbacteria              0              1          2          0
Blastocatellia            328            309        336        243
Chlamydiae                  3              6         25         23
Chloroflexia              789            666        441        825
Chthonomonadetes            0              0          0          0
Clostridia                 16              8         13         13
Coriobacteriia              0              0          1          0
Dehalococcoidia            97            155         70         98
Deinococci                 29             44         89         28
Deltaproteobacteria      3001           3141       4330       2154
Elusimicrobia               2              2          6          0
Entotheonellia            164            221        125        122
Erysipelotrichia            0              5          0          1
FFCH5909                    0              1          0          0
Fibrobacteria              36             46         45         35
Fimbriimonadia             43             32         69         29
...                       ...            ...        ...        ...
Nitrospira                 70             74         32         34
OLB14                      56             44         23         24
OM190                       0              0          0          0
Oxyphotobacteria          877           1711       2798        962
P2-11E                      3              3          7          3
Parcubacteria               2              0          3          1
Phycisphaerae              17             18        101        128
Pla4                        8              3          8          4
Planctomycetacia          283            247        357        710
Rhodothermia                5             10          0         11
Rubrobacteria            1974           2380       1351       1505
S0134                     114             73        116         75
SHA-26                      4             16          4         12
Saccharimonadia            30             49        130         57
Sericytochromatia          27             33         53         25
Spirochaetia                0              0          0          1
Subgroup                  501            681        385        284
Synergistia                 0              0          0          0
TK10                      611            522        275        583
Thermoanaerobaculia       146            122        117        127
Thermodesulfovibrionia      0              0          0          0
Thermoleophilia          3562           3733       2745       4643
Thermoplasmata              4              5         14         14
Unclassified             1216           1292       1211       1210
Verrucomicrobiae         1029           1391       1310        620
WS6                         1              2          0          0
WWE3                        0              0   

In [7]:
df2_std

Enzyme                       TGIRT  SuperScriptIV   Promega42   Promega55
Class                                                                    
0319-7L14                56.389715      50.257338   85.207394   81.041964
ABY1                      0.000000       0.000000    0.000000    0.000000
AKAU4049                  1.095445       0.894427    0.000000    0.447214
Acidimicrobiia           55.410288      46.301188  109.917242   47.300106
Acidobacteriia           28.455228      18.088670   29.364945    6.942622
Actinobacteria          274.296919     223.156895  445.351771  581.639321
Alphaproteobacteria     382.188435     303.496787  481.747652  232.488279
Anaerolineae              5.805170      12.700394    7.563068    8.093207
Armatimonadia             0.547723       0.447214    0.447214    2.863564
BD2-11                    6.730527       8.820431    5.761944    7.987490
BD7-11                    0.000000       1.095445    1.341641    0.836660
Babeliae                  1.303840       0.547723    1.923538    1.870829
Bacilli                  65.076878      74.751589  133.784155   60.870354
Bacteroidia             194.803747     143.224649  141.663333  188.279845
Berkelbacteria            0.000000       0.447214    0.894427    0.000000
Blastocatellia           36.929663      33.899853   31.546791   14.876155
Chlamydiae                0.547723       0.836660    7.516648    4.878524
Chloroflexia             33.729809      33.714982   39.232639   12.389512
Chthonomonadetes          0.000000       0.000000    0.000000    0.000000
Clostridia                2.280351       3.049590    2.792848    2.701851
Coriobacteriia            0.000000       0.000000    0.447214    0.000000
Dehalococcoidia           9.476286      14.525839    5.873670   11.104053
Deinococci                3.962323       4.147288   19.917329    2.966479
Deltaproteobacteria      48.864097      78.349856  440.766945  215.612384
Elusimicrobia             0.894427       0.547723    1.788854    0.000000
Entotheonellia           23.488295      34.629467   23.430749   22.074873
Erysipelotrichia          0.000000       2.236068    0.000000    0.447214
FFCH5909                  0.000000       0.447214    0.000000    0.000000
Fibrobacteria             2.949576       2.489980    3.000000    3.082207
Fimbriimonadia            3.646917       4.098780    7.596052    3.834058
...                            ...            ...         ...         ...
Nitrospira                8.689074       9.808160    4.037326    3.768289
OLB14                     2.949576       3.492850    4.722288    2.167948
OM190                     0.000000       0.000000    0.000000    0.000000
Oxyphotobacteria        139.263419     212.430459  523.532520  243.335776
P2-11E                    0.894427       0.894427    3.130495    1.341641
Parcubacteria             0.547723       0.000000    1.341641    0.447214
Phycisphaerae             1.341641       3.049590    5.630275   11.058933
Pla4                      0.547723       1.341641    3.049590    0.836660
Planctomycetacia         16.531788      16.577093   20.329781   50.906778
Rhodothermia              2.236068       1.224745    0.000000    4.381780
Rubrobacteria           158.676400     193.530359   67.310475   71.333723
S0134                    30.654527      18.796276   32.645061   13.619838
SHA-26                    0.836660       1.483240    0.836660    1.949359
Saccharimonadia           9.110434      16.452963   19.798990    4.393177
Sericytochromatia         2.073644       3.361547    9.071935    4.898979
Spirochaetia              0.000000       0.000000    0.000000    0.447214
Subgroup                 42.710654      44.549972   51.200586   37.036469
Synergistia               0.000000       0.000000    0.000000    0.000000
TK10                     43.888495      38.448667   25.951879   45.970643
Thermoanaerobaculia      16.269604      11.567195   11.436783   10.285913
Thermodesulfovibrionia    0.000000       0.000000    0.000000    0.000000
Ther

The data frame is simplified to only a class level information, OTU names, GC content and the four enzymatic conditions. 

In [8]:
# Copy of the original data frame
df2 = df1.copy()
# Dividing the per/enzyme values by an average to normalize them
df2 = df2.div(df2_ave)

# Sorting out the rest
df2 = df2.reset_index()
df3 = df2.drop(["Domain","Phylum", "Order", "Family", "Genus"], axis=1)
df3

/home/adam/Programs/anaconda3/lib/python3.6/site-packages/pandas/core/generic.py:3812: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_axis = axis.drop(labels, errors=errors)


Enzyme                   Class      OTU GC_content     TGIRT            \
Replicate                                                  1         4   
Name                                                Osnat037  Osnat040   
0             Oxyphotobacteria  Otu0001   0.547847  0.034208  0.294185   
1               Actinobacteria  Otu0002   0.572127  0.040782  0.026249   
2          Alphaproteobacteria  Otu0003   0.579208  0.013080  0.035285   
3          Gammaproteobacteria  Otu0004   0.550117  0.020963  0.001165   
4          Alphaproteobacteria  Otu0005   0.559406  0.015260  0.024384   
5          Alphaproteobacteria  Otu0006   0.522277  0.020266  0.008236   
6          Alphaproteobacteria  Otu0007   0.564356  0.003795  0.005894   
7          Alphaproteobacteria  Otu0008   0.559406  0.008397  0.008317   
8          Alphaproteobacteria  Otu0009   0.574257  0.001857  0.003310   
9          Deltaproteobacteria  Otu0010   0.567757  0.037321  0.051649   
10               Rubrobacteria  Otu0011   0.602804  0.024823  0.049139   
11              Actinobacteria  Otu0012   0.586797  0.021844  0.035585   
12              Actinobacteria  Otu0013   0.581907  0.011451  0.003083   
13               Rubrobacteria  Otu0014   0.593458  0.012158  0.021277   
14              Actinobacteria  Otu0015   0.610294  0.008280  0.020435   
15              Actinobacteria  Otu0016   0.572127  0.003171  0.002378   
16         Alphaproteobacteria  Otu0017   0.547030  0.008074  0.001696   
17         Gammaproteobacteria  Otu0018   0.533800  0.000000  0.000000   
18         Deltaproteobacteria  Otu0019   0.565421  0.004665  0.011663   
19         Gammaproteobacteria  Otu0020   0.545455  0.000000  0.000000   
20         Alphaproteobacteria  Otu0021   0.576733  0.002826  0.002342   
21         Alphaproteobacteria  Otu0022   0.576733  0.003068  0.002745   
22         Alphaproteobacteria  Otu0023   0.529703  0.000000  0.000000   
23         Alphaproteobacteria  Otu0024   0.586634  0.000484  0.004199   
24         Alphaproteobacteria  Otu0025   0.564356  0.002665  0.005491   
25              Actinobacteria  Otu0026   0.581907  0.006166  0.008016   
26              Actinobacteria  Otu0027   0.584352  0.001850  0.006518   
27                 Bacteroidia  Otu0028   0.508274  0.000333  0.008652   
28         Gammaproteobacteria  Otu0029   0.536131  0.001165  0.000000   
29             Thermoleophilia  Otu0030   0.585082  0.020775  0.016283   
...                        ...      ...        ...       ...       ...   
8602           Thermoleophilia  Otu8603   0.592075  0.000000  0.000000   
8603             Elusimicrobia  Otu8604   0.549528  0.000000  0.000000   
8604            Acidimicrobiia  Otu8605   0.595533  0.000000  0.000000   
8605                  Subgroup  Otu8606   0.593458  0.001996  0.000000   
8606              Unclassified  Otu8607   0.474453  0.000000  0.000000   
8607              Unclassified  Otu8608   0.519814  0.000000  0.000000   
8608                   Bacilli  Otu8609   0.551402  0.000000  0.000000   
8609          Planctomycetacia  Otu8610   0.544335  0.000000  0.000000   
8610       Gammaproteobacteria  Otu8611   0.552448  0.000000  0.000000   
8611            Entotheonellia  Otu8612   0.558313  0.000000  0.000000   
8612       Deltaproteobacteria  Otu8613   0.586047  0.000000  0.000000   
8613       Alphaproteobacteria  Otu8614   0.533499  0.000081  0.000000   
8614       Gammaproteobacteria  Otu8615   0.572093  0.000000  0.000000   
8615                Chlamydiae  Otu8616   0.517483  0.000000  0.000000   
8616              Unclassified  Otu8617   0.542056  0.000000  0.000000   
8617       Deltaproteobacteria  Otu8618   0.561772  0.000000  0.000000   
8618                    BD2-11  Otu8619   0.602326  0.000000  0.000000   
8619       Alphaproteobacteria  Otu8620   0.574257  0.000000  0.000000   
8620       Gammaproteobacteria  Otu8621   0.565421  0.000000  0.000000   
8621          Planctomycetacia  Otu8622   0.654846  0.000000  0.000000   
8622

The resulting data frame is "melted" such that the enzymatic conditions become a new column and the GC content and value are the only two numerical value columns.

In [9]:
df4 = df3.melt(id_vars=["Class", "OTU", "GC_content"])

By summarizing within each Class and Enzyme category, we should receive either 1 or 0 if a group is not present in a given category. 

In [10]:
df4.groupby(["Class", "Enzyme"]).sum()

GC_content  value
Class               Enzyme                           
0319-7L14           Promega42       164.067946    1.0
                    Promega55       164.067946    1.0
                    SuperScriptIV   164.067946    1.0
                    TGIRT           164.067946    1.0
ABY1                Promega42         2.616708    0.0
                    Promega55         2.616708    0.0
                    SuperScriptIV     2.616708    0.0
                    TGIRT             2.616708    0.0
AKAU4049            Promega42         5.941860    0.0
                    Promega55         5.941860    1.0
                    SuperScriptIV     5.941860    1.0
                    TGIRT             5.941860    1.0
Acidimicrobiia      Promega42       754.650489    1.0
                    Promega55       754.650489    1.0
                    SuperScriptIV   754.650489    1.0
                    TGIRT           754.650489    1.0
Acidobacteriia      Promega42        85.696517    1.0
                    Promega55        85.696517    1.0
                    SuperScriptIV    85.696517    1.0
                    TGIRT            85.696517    1.0
Actinobacteria      Promega42      1776.356219    1.0
                    Promega55      1776.356219    1.0
                    SuperScriptIV  1776.356219    1.0
                    TGIRT          1776.356219    1.0
Alphaproteobacteria Promega42      2091.323969    1.0
                    Promega55      2091.323969    1.0
                    SuperScriptIV  2091.323969    1.0
                    TGIRT          2091.323969    1.0
Anaerolineae        Promega42       223.974348    1.0
                    Promega55       223.974348    1.0
...                                        ...    ...
Thermoplasmata      SuperScriptIV    28.834197    1.0
                    TGIRT            28.834197    1.0
Unclassified        Promega42      2280.289557    1.0
                    Promega55      2280.289557    1.0
                    SuperScriptIV  2280.289557    1.0
                    TGIRT          2280.289557    1.0
Verrucomicrobiae    Promega42       760.390122    1.0
                    Promega55       760.390122    1.0
                    SuperScriptIV   760.390122    1.0
                    TGIRT           760.390122    1.0
WS6                 Promega42        14.654898    0.0
                    Promega55        14.654898    0.0
                    SuperScriptIV    14.654898    1.0
                    TGIRT            14.654898    1.0
WWE3                Promega42         2.561881    0.0
                    Promega55         2.561881    0.0
                    SuperScriptIV     2.561881    0.0
                    TGIRT             2.561881    0.0
Woesearchaeia       Promega42         2.634961    0.0
                    Promega55         2.634961    1.0
                    SuperScriptIV     2.634961    0.0
                    TGIRT             2.634961    0.0
uncultured          Promega42       301.165428    1.0
                    Promega55       301.165428    1.0
                    SuperScriptIV   301.165428    1.0
                    TGIRT           301.165428    1.0
vadinHA49           Promega42        17.050986    1.0
                    Promega55        17.050986    1.0
                    SuperScriptIV    17.050986    1.0
                    TGIRT            17.050986    1.0

[324 rows x 2 columns]

Multiplying a GC content value of each OTU by the OTU's relative abundance within a given Class and Enzyme group, we receive the OTU's proportional contribution to the overall Class GC content. By summarizing the GC content over a Class, we obtain it's weighted average GC content. The Class normalized count is discarded. 

In [11]:
df4.GC_content = df4.GC_content*df4.value
df5 = df4.groupby(["Class","Enzyme"]).sum()
df5 = df5.drop("value", axis=1)
df5 

GC_content
Class               Enzyme                   
0319-7L14           Promega42        0.580750
                    Promega55        0.582987
                    SuperScriptIV    0.581233
                    TGIRT            0.582942
ABY1                Promega42        0.000000
                    Promega55        0.000000
                    SuperScriptIV    0.000000
                    TGIRT            0.000000
AKAU4049            Promega42        0.000000
                    Promega55        0.593023
                    SuperScriptIV    0.593798
                    TGIRT            0.594186
Acidimicrobiia      Promega42        0.585221
                    Promega55        0.586662
                    SuperScriptIV    0.588191
                    TGIRT            0.587488
Acidobacteriia      Promega42        0.555791
                    Promega55        0.561708
                    SuperScriptIV    0.561813
                    TGIRT            0.559804
Actinobacteria      Promega42        0.583321
                    Promega55        0.583805
                    SuperScriptIV    0.584725
                    TGIRT            0.586320
Alphaproteobacteria Promega42        0.554835
                    Promega55        0.553426
                    SuperScriptIV    0.562606
                    TGIRT            0.563610
Anaerolineae        Promega42        0.552375
                    Promega55        0.559423
...                                       ...
Thermoplasmata      SuperScriptIV    0.580311
                    TGIRT            0.577720
Unclassified        Promega42        0.492766
                    Promega55        0.507756
                    SuperScriptIV    0.505267
                    TGIRT            0.503933
Verrucomicrobiae    Promega42        0.534486
                    Promega55        0.533333
                    SuperScriptIV    0.532315
                    TGIRT            0.532096
WS6                 Promega42        0.000000
                    Promega55        0.000000
                    SuperScriptIV    0.496296
                    TGIRT            0.496296
WWE3                Promega42        0.000000
                    Promega55        0.000000
                    SuperScriptIV    0.000000
                    TGIRT            0.000000
Woesearchaeia       Promega42        0.000000
                    Promega55        0.526992
                    SuperScriptIV    0.000000
                    TGIRT            0.000000
uncultured          Promega42        0.608757
                    Promega55        0.612651
                    SuperScriptIV    0.611116
                    TGIRT            0.616270
vadinHA49           Promega42        0.568613
                    Promega55        0.569948
                    SuperScriptIV    0.570093
                    TGIRT            0.570093

[324 rows x 1 columns]

In [43]:
df2_ave2 = df2_ave.reset_index()
df2_ave2 = df2_ave2.melt(id_vars="Class")
df2_ave2 = df2_ave2.set_index(["Class", "Enzyme"])
df2_ave2 = df2_ave2.sort_values(["Class", "Enzyme"])
# Renaming the values column to have neater output
df2_ave2.rename(columns={"value":"Average"},level=0, inplace=True)
df2_ave2

Average
Class               Enzyme                
0319-7L14           Promega42          527
                    Promega55          442
                    SuperScriptIV      332
                    TGIRT              392
ABY1                Promega42            0
                    Promega55            0
                    SuperScriptIV        0
                    TGIRT                0
AKAU4049            Promega42            0
                    Promega55            1
                    SuperScriptIV        3
                    TGIRT                4
Acidimicrobiia      Promega42         1203
                    Promega55         1617
                    SuperScriptIV     1518
                    TGIRT             1858
Acidobacteriia      Promega42          257
                    Promega55          259
                    SuperScriptIV      444
                    TGIRT              359
Actinobacteria      Promega42         5864
                    Promega55        11263
                    SuperScriptIV    10105
                    TGIRT            11353
Alphaproteobacteria Promega42        12943
                    Promega55         9302
                    SuperScriptIV    12148
                    TGIRT            12385
Anaerolineae        Promega42          191
                    Promega55          175
...                                    ...
Thermoplasmata      SuperScriptIV        5
                    TGIRT                4
Unclassified        Promega42         1211
                    Promega55         1210
                    SuperScriptIV     1292
                    TGIRT             1216
Verrucomicrobiae    Promega42         1310
                    Promega55          620
                    SuperScriptIV     1391
                    TGIRT             1029
WS6                 Promega42            0
                    Promega55            0
                    SuperScriptIV        2
                    TGIRT                1
WWE3                Promega42            0
                    Promega55            0
                    SuperScriptIV        0
                    TGIRT                0
Woesearchaeia       Promega42            0
                    Promega55            2
                    SuperScriptIV        0
                    TGIRT                0
uncultured          Promega42           41
                    Promega55           66
                    SuperScriptIV       31
                    TGIRT               28
vadinHA49           Promega42            7
                    Promega55            7
                    SuperScriptIV        1
                    TGIRT                1

[324 rows x 1 columns]

In [42]:
df2_std2 = df2_std.reset_index()
df2_std2 = df2_std2.melt(id_vars="Class")
df2_std2 = df2_std2.set_index(["Class", "Enzyme"])
df2_std2 = df2_std2.sort_values(["Class", "Enzyme"])
# Renaming the values column to have neater output
df2_std2.rename(columns={"value":"StdDev"},level=0, inplace=True)
df2_std2

StdDev
Class               Enzyme                   
0319-7L14           Promega42       85.207394
                    Promega55       81.041964
                    SuperScriptIV   50.257338
                    TGIRT           56.389715
ABY1                Promega42        0.000000
                    Promega55        0.000000
                    SuperScriptIV    0.000000
                    TGIRT            0.000000
AKAU4049            Promega42        0.000000
                    Promega55        0.447214
                    SuperScriptIV    0.894427
                    TGIRT            1.095445
Acidimicrobiia      Promega42      109.917242
                    Promega55       47.300106
                    SuperScriptIV   46.301188
                    TGIRT           55.410288
Acidobacteriia      Promega42       29.364945
                    Promega55        6.942622
                    SuperScriptIV   18.088670
                    TGIRT           28.455228
Actinobacteria      Promega42      445.351771
                    Promega55      581.639321
                    SuperScriptIV  223.156895
                    TGIRT          274.296919
Alphaproteobacteria Promega42      481.747652
                    Promega55      232.488279
                    SuperScriptIV  303.496787
                    TGIRT          382.188435
Anaerolineae        Promega42        7.563068
                    Promega55        8.093207
...                                       ...
Thermoplasmata      SuperScriptIV    1.000000
                    TGIRT            0.836660
Unclassified        Promega42       40.947527
                    Promega55       21.505813
                    SuperScriptIV   33.328666
                    TGIRT           40.133527
Verrucomicrobiae    Promega42       84.882271
                    Promega55       43.312816
                    SuperScriptIV  112.839266
                    TGIRT           49.726251
WS6                 Promega42        0.000000
                    Promega55        0.000000
                    SuperScriptIV    0.894427
                    TGIRT            0.447214
WWE3                Promega42        0.000000
                    Promega55        0.000000
                    SuperScriptIV    0.000000
                    TGIRT            0.000000
Woesearchaeia       Promega42        0.000000
                    Promega55        0.894427
                    SuperScriptIV    0.000000
                    TGIRT            0.000000
uncultured          Promega42        4.438468
                    Promega55        3.420526
                    SuperScriptIV    1.923538
                    TGIRT            2.701851
vadinHA49           Promega42        1.949359
                    Promega55        1.673320
                    SuperScriptIV    0.447214
                    TGIRT            0.447214

[324 rows x 1 columns]

In [44]:
dfFinal = pd.concat([df2_ave2, df2_std2, df5],axis=1)
dfFinal

Average      StdDev  GC_content
Class               Enzyme                                        
0319-7L14           Promega42          527   85.207394    0.580750
                    Promega55          442   81.041964    0.582987
                    SuperScriptIV      332   50.257338    0.581233
                    TGIRT              392   56.389715    0.582942
ABY1                Promega42            0    0.000000    0.000000
                    Promega55            0    0.000000    0.000000
                    SuperScriptIV        0    0.000000    0.000000
                    TGIRT                0    0.000000    0.000000
AKAU4049            Promega42            0    0.000000    0.000000
                    Promega55            1    0.447214    0.593023
                    SuperScriptIV        3    0.894427    0.593798
                    TGIRT                4    1.095445    0.594186
Acidimicrobiia      Promega42         1203  109.917242    0.585221
                    Promega55         1617   47.300106    0.586662
                    SuperScriptIV     1518   46.301188    0.588191
                    TGIRT             1858   55.410288    0.587488
Acidobacteriia      Promega42          257   29.364945    0.555791
                    Promega55          259    6.942622    0.561708
                    SuperScriptIV      444   18.088670    0.561813
                    TGIRT              359   28.455228    0.559804
Actinobacteria      Promega42         5864  445.351771    0.583321
                    Promega55        11263  581.639321    0.583805
                    SuperScriptIV    10105  223.156895    0.584725
                    TGIRT            11353  274.296919    0.586320
Alphaproteobacteria Promega42        12943  481.747652    0.554835
                    Promega55         9302  232.488279    0.553426
                    SuperScriptIV    12148  303.496787    0.562606
                    TGIRT            12385  382.188435    0.563610
Anaerolineae        Promega42          191    7.563068    0.552375
                    Promega55          175    8.093207    0.559423
...                                    ...         ...         ...
Thermoplasmata      SuperScriptIV        5    1.000000    0.580311
                    TGIRT                4    0.836660    0.577720
Unclassified        Promega42         1211   40.947527    0.492766
                    Promega55         1210   21.505813    0.507756
                    SuperScriptIV     1292   33.328666    0.505267
                    TGIRT             1216   40.133527    0.503933
Verrucomicrobiae    Promega42         1310   84.882271    0.534486
                    Promega55          620   43.312816    0.533333
                    SuperScriptIV     1391  112.839266    0.532315
                    TGIRT             1029   49.726251    0.532096
WS6                 Promega42            0    0.000000    0.000000
                    Promega55            0    0.000000    0.000000
                    SuperScriptIV        2    0.894427    0.496296
                    TGIRT                1    0.447214    0.496296
WWE3                Promega42            0    0.000000    0.000000
                    Promega55            0    0.000000    0.000000
                    SuperScriptIV        0    0.000000    0.000000
                    TGIRT                0    0.000000    0.000000
Woesearchaeia       Promega42            0    0.000000    0.000000
                    Promega55            2    0.894427    0.526992
                    SuperScriptIV        0    0.000000    0.000000
                    TGIRT                0    0.000000    0.000000
uncultured          Promega42           41    4.438468    0.608757
                    Promega55           66    3.420526    0.612651
                    SuperScriptIV       31    1.923538    0.611116
                    TGIRT               28    2.701851    0.616270
vadinHA49           Promega42            7    1.949359    0.568613
               

In [45]:
dfFinal = dfFinal.reset_index()
dfFinal = dfFinal.pivot(index="Class", columns="Enzyme")
dfFinal

Average                                     StdDev  \
Enzyme                 Promega42 Promega55 SuperScriptIV  TGIRT   Promega42   
Class                                                                         
0319-7L14                    527       442           332    392   85.207394   
ABY1                           0         0             0      0    0.000000   
AKAU4049                       0         1             3      4    0.000000   
Acidimicrobiia              1203      1617          1518   1858  109.917242   
Acidobacteriia               257       259           444    359   29.364945   
Actinobacteria              5864     11263         10105  11353  445.351771   
Alphaproteobacteria        12943      9302         12148  12385  481.747652   
Anaerolineae                 191       175           113     89    7.563068   
Armatimonadia                  6        19             1      2    0.447214   
BD2-11                        26        33            48     42    5.761944   
BD7-11                         7         4             4      0    1.341641   
Babeliae                      11        10            18      9    1.923538   
Bacilli                     1356       656           663    520  133.784155   
Bacteroidia                 2825      1817          2307   3005  141.663333   
Berkelbacteria                 2         0             1      0    0.894427   
Blastocatellia               336       243           309    328   31.546791   
Chlamydiae                    25        23             6      3    7.516648   
Chloroflexia                 441       825           666    789   39.232639   
Chthonomonadetes               0         0             0      0    0.000000   
Clostridia                    13        13             8     16    2.792848   
Coriobacteriia                 1         0             0      0    0.447214   
Dehalococcoidia               70        98           155     97    5.873670   
Deinococci                    89        28            44     29   19.917329   
Deltaproteobacteria         4330      2154          3141   3001  440.766945   
Elusimicrobia                  6         0             2      2    1.788854   
Entotheonellia               125       122           221    164   23.430749   
Erysipelotrichia               0         1             5      0    0.000000   
FFCH5909                       0         0             1      0    0.000000   
Fibrobacteria                 45        35            46     36    3.000000   
Fimbriimonadia                69        29            32     43    7.596052   
...                          ...       ...           ...    ...         ...   
Nitrospira                    32        34            74     70    4.037326   
OLB14                         23        24            44     56    4.722288   
OM190                          0         0             0      0    0.000000   
Oxyphotobacteria            2798       962          1711    877  523.532520   
P2-11E                         7         3             3      3    3.130495   
Parcubacteria                  3         1             0      2    1.341641   
Phycisphaerae                101       128            18     17    5.630275   
Pla4                           8         4             3      8    3.049590   
Planctomycetacia             357       710           247    283   20.329781   
Rhodothermia                   0        11            10      5    0.000000   
Rubrobacteria               1351      1505          2380   1974   67.310475   
S0134                        116        75            73    114   32.645061   
SHA-26                         4        12            16      4    0.836660   
Saccharimonadia              130        57            49     30   19.798990   
Sericytochromatia             53        25            33     27    9.071935   
Spirochaetia                   0         1             0      0    0.000000   
Subgroup                     385       284           681    501   51.200586

In [46]:
dfFinal.to_csv("GC_class_whole.csv")

Only bacterial classes that account for the upper quartile of the dataset will be plotted. The remaining groups are summarized and labeled as "Low abundance".

In [61]:
# Using row sums to normalize each class
rowSums = dfFinal.sum(axis=1, level=0)["Average"]

# 85 % quantile
quantile85 = rowSums.quantile(q=0.5)
rowSumsVector = rowSums <= quantile85

# Upper 85% quantile rows
df3 = dfFinal.loc[rowSums >= quantile85, :]
la = dfFinal.loc[rowSums < quantile85, :].sum(axis=0)

In [62]:
# Pulling lower quantile rows together and appending them to the upper quantile data frame
la = la.to_frame(name="Low abundance")
la = la.transpose()

df3 = df3.append(la)
df3

Average                                       StdDev  \
Enzyme              Promega42 Promega55 SuperScriptIV    TGIRT   Promega42   
0319-7L14               527.0     442.0         332.0    392.0   85.207394   
Acidimicrobiia         1203.0    1617.0        1518.0   1858.0  109.917242   
Acidobacteriia          257.0     259.0         444.0    359.0   29.364945   
Actinobacteria         5864.0   11263.0       10105.0  11353.0  445.351771   
Alphaproteobacteria   12943.0    9302.0       12148.0  12385.0  481.747652   
Anaerolineae            191.0     175.0         113.0     89.0    7.563068   
BD2-11                   26.0      33.0          48.0     42.0    5.761944   
Bacilli                1356.0     656.0         663.0    520.0  133.784155   
Bacteroidia            2825.0    1817.0        2307.0   3005.0  141.663333   
Blastocatellia          336.0     243.0         309.0    328.0   31.546791   
Chloroflexia            441.0     825.0         666.0    789.0   39.232639   
Dehalococcoidia          70.0      98.0         155.0     97.0    5.873670   
Deinococci               89.0      28.0          44.0     29.0   19.917329   
Deltaproteobacteria    4330.0    2154.0        3141.0   3001.0  440.766945   
Entotheonellia          125.0     122.0         221.0    164.0   23.430749   
Fibrobacteria            45.0      35.0          46.0     36.0    3.000000   
Fimbriimonadia           69.0      29.0          32.0     43.0    7.596052   
Gammaproteobacteria    5967.0    7610.0        2793.0   2576.0  556.201672   
Gemmatimonadetes        532.0     591.0         518.0    463.0  111.576431   
Gitt-GS-136             270.0     171.0         239.0    274.0   32.893768   
Holophagae              235.0     139.0         308.0    191.0   25.416530   
JG30-KF-CM66             76.0     145.0         175.0    175.0   11.278298   
KD4-96                  298.0     264.0         370.0    406.0   21.173096   
Ktedonobacteria          26.0      41.0          61.0     52.0    3.563706   
Longimicrobia           328.0     217.0         213.0    197.0   36.956731   
MB-A2-108                61.0     101.0          67.0     99.0   14.754660   
Nitriliruptoria         253.0     380.0         410.0    408.0   17.840964   
Nitrospira               32.0      34.0          74.0     70.0    4.037326   
Oxyphotobacteria       2798.0     962.0        1711.0    877.0  523.532520   
Phycisphaerae           101.0     128.0          18.0     17.0    5.630275   
Planctomycetacia        357.0     710.0         247.0    283.0   20.329781   
Rubrobacteria          1351.0    1505.0        2380.0   1974.0   67.310475   
S0134                   116.0      75.0          73.0    114.0   32.645061   
Saccharimonadia         130.0      57.0          49.0     30.0   19.798990   
Subgroup                385.0     284.0         681.0    501.0   51.200586   
TK10                    275.0     583.0         522.0    611.0   25.951879   
Thermoanaerobaculia     117.0     127.0         122.0    146.0   11.436783   
Thermoleophilia        2745.0    4643.0        3733.0   3562.0  254.825430   
Unclassified           1211.0    1210.0        1292.0   1216.0   40.947527   
Verrucomicrobiae       1310.0     620.0        1391.0   1029.0   84.882271   
uncultured               41.0      66.0          31.0     28.0    4.438468   
Low abundance           288.0     239.0         230.0    211.0   68.925165   

                                                          GC_content  \
Enzyme                Promega55 SuperScriptIV       TGIRT  Promega42   
0319-7L14             81.041964     50.257338   56.389715   0.580750   
Acidimicrobiia        47.300106     46.301188   55.410288   0.585221   
Acidobacteriia         6.942622     18.088670   28.455228   0.555791   
Actinobacteria       581.639321    223.156895  274.296919   0.583321   
Alphaproteobacteria  232.488279    303.496787  382.188435   0.554835   
Anaerolineae           8.093207     12.700394    5.805170   0.552375   
BD2-11       

In [58]:
df3.to_csv("GC_class_forFigure.csv")

In [63]:
df3.to_csv("barplot_data_class.csv")

In [55]:
df3

index variable     value
0               0319-7L14  level_0         0
1          Acidimicrobiia  level_0         1
2          Acidobacteriia  level_0         2
3          Actinobacteria  level_0         3
4     Alphaproteobacteria  level_0         4
5            Anaerolineae  level_0         5
6                  BD2-11  level_0         6
7                 Bacilli  level_0         7
8             Bacteroidia  level_0         8
9          Blastocatellia  level_0         9
10           Chloroflexia  level_0        10
11        Dehalococcoidia  level_0        11
12             Deinococci  level_0        12
13    Deltaproteobacteria  level_0        13
14         Entotheonellia  level_0        14
15          Fibrobacteria  level_0        15
16         Fimbriimonadia  level_0        16
17    Gammaproteobacteria  level_0        17
18       Gemmatimonadetes  level_0        18
19            Gitt-GS-136  level_0        19
20             Holophagae  level_0        20
21           JG30-KF-CM66  level_0        21
22                 KD4-96  level_0        22
23        Ktedonobacteria  level_0        23
24          Longimicrobia  level_0        24
25              MB-A2-108  level_0        25
26        Nitriliruptoria  level_0        26
27             Nitrospira  level_0        27
28       Oxyphotobacteria  level_0        28
29          Phycisphaerae  level_0        29
...                   ...      ...       ...
6018           Deinococci    value  0.564073
6019  Deltaproteobacteria    value  0.565658
6020       Entotheonellia    value  0.575045
6021        Fibrobacteria    value  0.553822
6022       Fimbriimonadia    value  0.541226
6023  Gammaproteobacteria    value  0.545745
6024     Gemmatimonadetes    value  0.628619
6025          Gitt-GS-136    value  0.560207
6026           Holophagae    value  0.568013
6027         JG30-KF-CM66    value  0.597318
6028               KD4-96    value  0.568869
6029      Ktedonobacteria    value  0.580245
6030        Longimicrobia    value  0.614556
6031            MB-A2-108    value  0.605956
6032      Nitriliruptoria    value  0.577517
6033           Nitrospira    value  0.599818
6034     Oxyphotobacteria    value  0.545485
6035        Phycisphaerae    value  0.577386
6036     Planctomycetacia    value  0.619704
6037        Rubrobacteria    value  0.601583
6038                S0134    value  0.598523
6039      Saccharimonadia    value   0.49659
6040             Subgroup    value  0.580671
6041                 TK10    value   0.61698
6042  Thermoanaerobaculia    value  0.582521
6043      Thermoleophilia    value  0.589915
6044         Unclassified    value  0.503933
6045     Verrucomicrobiae    value  0.532096
6046           uncultured    value   0.61627
6047        Low abundance    value   11.6263

[6048 rows x 3 columns]

In [ ]:
# Simplifying a multi index into just one index 
idx = pd.IndexSlice

df1 = data.data.copy()

df1 = df1.sum(level="Enzyme", axis=1)

df1 = df1.reset_index()

df1 = df1.iloc[:,1:]

df1 = df1.iloc[:,[1,5,6,7,8,9,10]]

In [ ]:
df1.index = df1.OTU

df1 = df1.drop("OTU", axis=1)

In [ ]:
colNames = list(df1.columns.get_level_values("Enzyme"))
colNames[1] = "GC"
colNames

df1.columns = colNames

del df1.index.name

In [ ]:
df1melted = df1.melt(id_vars=["Class", "GC"])
df1melted

In [ ]:
colSum = df1melted.groupby("variable").sum()["value"]

colSum["Promega42"]

newValue = []
# Dividing each row value by an appropriate total sum of the category (enzyme)
for row in df1melted.iterrows():
    newValue.append(row[1].value/colSum[row[1].variable])
    
df1melted["value"] = newValue

In [ ]:
df1sum = df1melted.groupby(["Class", "variable"]).sum()

In [ ]:
df1melted.groupby(["Class", "variable"]).mean()

In [ ]:
for row in df1melted.iterrows():
    # For a future convenience
    row=row[1]
    classval = row.Class
    enzyme = row.variable
    print(classval, enzyme)
    break

In [ ]:
idx = pd.IndexSlice
df1sum.loc[idx[classval, enzyme],idx["value"]]

In [ ]:
df1sum.loc[idx[classval, enzyme],:]

In [ ]:
df1.to_csv("data_for_gc_plot.csv")

|Enzyme        |TGIRT  |SuperScriptIV|Promega42  |Promega55|
|:-------------|:-----:|:-----------:|:---------:|:-------:|
|TGIRT         | x     | TvS         | Tv42      | Tv55    |  
|SuperScriptIV | TvS   | x           | Sv42      | Sv55    |
|Promega42     | Tv42  | Sv42        | x         | P42v55  |
|Promega55     | Tv55  | Sv55        | P42v55    | x       |